In [6]:
day = 14
from IPython.display import IFrame
url = "https://adventofcode.com/2022/day/%d"%(day)
IFrame(src=url, width=1000, height=600)

In [153]:
import urllib.request
import sys
from timeit import default_timer as timer
import itertools


def gather_input_data(url, sessionId, transform=lambda x: str(x, "utf-8").strip('\n')):
    request = urllib.request.Request(url)
    request.add_header("cookie", "session={}".format(sessionId)) # Source the data directly from AoC

    values = []
    with urllib.request.urlopen(request) as data:
        for line in data:
            values.append(transform(line))

    return values

def get_data(day, year=2022):
    with open('sessionID') as f:
        sessionId = f.readlines()[0]
    url = "https://adventofcode.com/%d/day/%d/input"%(year,day)
    data = gather_input_data(url, sessionId)
    return data

def read_file(filename):
    # read file
    with open(filename) as f:
        lines = f.readlines()
    output = [str.rstrip(line) for line in lines]    
    return output

def parse(val):
    line = []
    for coord in val.split(' -> '):
        col,row = coord.split(',')
        out = (int(row), int(col))
        line.append(out)
    return line

def fill_map(a,b,cave_map):
    if a[0] == b[0]:
        s,e = sorted([a[1],b[1]])
        cave_map[a[0], s:e+1] = 1
    if a[1] == b[1]:
        s,e = sorted([a[0],b[0]])
        cave_map[s:e+1, a[1]] = 1
    return cave_map

def init_map(max_row, max_col, instructions):
    cave_map = np.zeros([max_row, max_col], int)   
    for line in instructions:
        endpoints = zip(line[:-1], line[1:])
        for a,b in endpoints:
            cave_map = fill_map(a,b, cave_map)
    return cave_map

In [220]:
test = False
data = get_data(day)
if test:
    data = read_file('test.txt')
    
map_instructions = [parse(val) for val in data]
max_col = max([val[1] for line in map_instructions for val in line])
max_row = max([val[0] for line in map_instructions for val in line])

import numpy as np
cave_map = init_map(max_row+1, max_col+1, map_instructions)


In [221]:
import plotly.express as px
px.imshow(cave_map)

In [222]:
 
def fall_sim(row, col):
        while True:
            #print('in\t',row,col)
            look_at_map = np.where(cave_map[row:,col]!=0)[0]
            if look_at_map.size == 0:
                return False
            else:
                row = look_at_map[0] - 1 + row
            #print('start\t',row,col)


            
            if cave_map[row+1, col-1] == 0:
                row += 1
                col -= 1
                #print('left\t',row,col)
                continue
            elif cave_map[row+1, col+1] == 0:
                row += 1
                col += 1
                #print('right\t',row,col)
                continue
            else:
                cave_map[row, col] = 2
                if (row==0) & (col==500) :
                    return False
                #print('plot\t',row,col,'\n\n')
                return True

In [223]:
count = 0
run = True
while(run):
    run = fall_sim(0,500)
    count+=1
print(count)

673


In [224]:
px.imshow(cave_map)

In [225]:
cave_map = init_map(max_row+3, max_col+199, map_instructions)
cave_map[-1,:] = 1
px.imshow(cave_map)

In [215]:
count = 0
run = True
while(run):
    run = fall_sim(0,500)
    count+=1
print(count)

KeyboardInterrupt: 

In [216]:
px.imshow(cave_map)

In [ ]:
import sys
import math
from copy import deepcopy
from collections import defaultdict, deque
infile = 'input.txt'
data = open(infile).read().strip()
lines = [x for x in data.split('\n')]

R = set()
for line in lines:
    prev = None
    for point in line.split('->'):
        x,y = point.split(',')
        x,y = int(x),int(y)
        if prev is not None:
            dx = x-prev[0]
            dy = y-prev[1]
            len_ = max(abs(dx),abs(dy))
            for i in range(len_+1):
                xx = prev[0]+i*(1 if dx>0 else (-1 if dx<0 else 0))
                yy = prev[1]+i*(1 if dy>0 else (-1 if dy<0 else 0))
                R.add((xx,yy))
        prev = (x,y)

floor = 2+max(r[1] for r in R)
#print(floor)
lo_x = min(r[0] for r in R)-2000
hi_x = max(r[0] for r in R)+2000
for x in range(lo_x, hi_x):
    R.add((x,floor))

did_p1 = False
for t in range(1000000):
    rock = (500,0)
    while True:
        if rock[1]+1>=floor and (not did_p1):
            did_p1 = True
            print(t)
        if (rock[0],rock[1]+1) not in R:
            rock = (rock[0],rock[1]+1)
        elif (rock[0]-1,rock[1]+1) not in R:
            rock = (rock[0]-1, rock[1]+1)
        elif (rock[0]+1, rock[1]+1) not in R:
            rock = (rock[0]+1, rock[1]+1)
        else:
            break
    if rock == (500,0):
        print(t+1)
        break
    R.add(rock)